In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import Pipeline

In [2]:
def process_wind_file(filepath):
    df = pd.read_table(filepath, delim_whitespace=True)
    df = df.drop(index=df.index[0])
    df['#YY'] = df['#YY'].apply(int)
    #print((filepath[14:18]))
    df = df[df['#YY'] == int(filepath[20:24])]

    for col in df.columns:
        df[col] = pd.to_numeric(df[col], errors='coerce')
    df = df.groupby(['MM','DD','#YY']).mean().reset_index()
    df.rename(columns={'#YY': 'year', 'MM': 'month', 'DD': 'day'}, inplace=True)
    #add time to df which has datetime
    df['time'] = pd.to_datetime(df[['year', 'month', 'day']])
    df['time'] = df['time'].dt.date
    return df[['time','WSPD']]

df = process_wind_file("Data/Wind_46025/wind2012.txt")
df

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)


time       WSPD
0    2012-01-01   1.595833
1    2012-01-02   3.631818
2    2012-01-03   3.058333
3    2012-01-04   2.629167
4    2012-01-05   3.387500
..          ...        ...
140  2012-12-27  10.887500
141  2012-12-28   5.126087
142  2012-12-29   3.704167
143  2012-12-30   3.520833
144  2012-12-31   4.604545

[145 rows x 2 columns]

In [3]:



# Generate a complete date range for 2010
all_dates = pd.date_range(start="2012-01-01", end="2012-12-31")

# Find the missing date
missing_date = all_dates.difference(df['time'])
print("Missing date:", missing_date)


Missing date: DatetimeIndex(['2012-04-01', '2012-04-02', '2012-04-03', '2012-04-04',
               '2012-04-05', '2012-04-06', '2012-04-07', '2012-04-08',
               '2012-04-09', '2012-04-19',
               ...
               '2012-11-14', '2012-11-15', '2012-11-16', '2012-11-17',
               '2012-11-18', '2012-11-19', '2012-11-20', '2012-11-21',
               '2012-11-22', '2012-11-23'],
              dtype='datetime64[ns]', length=221, freq=None)


In [4]:
fin_df = process_wind_file("Data/Wind_46025/wind2008.txt")
for i in range(2009, 2024, 1):
    #print(i)
    fin_df = pd.concat([fin_df, process_wind_file("Data/Wind_46025/wind" + str(i) + ".txt")])
fin_df

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated a

time      WSPD
0    2008-01-01  3.687500
1    2008-01-02  3.758333
2    2008-01-03  2.050000
3    2008-01-04  4.012500
4    2008-01-05  6.833333
..          ...       ...
360  2023-12-27  2.990972
361  2023-12-28  2.878472
362  2023-12-29  2.540972
363  2023-12-30  4.835417
364  2023-12-31  3.921528

[5617 rows x 2 columns]

In [5]:
def to_str(dt):
    return dt.strftime('%m/%d/%Y')
len(np.unique(fin_df['time'].apply(to_str)))
fin_df['time'].apply(to_str)[-4:]

361    12/28/2023
362    12/29/2023
363    12/30/2023
364    12/31/2023
Name: time, dtype: object

In [6]:
len(np.unique(process_wind_file("Data/Wind_46025/wind" + str(2013) + ".txt")['time']))

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)


365

In [7]:
process_wind_file("Data/Wind_46025/wind" + str(2012) + ".txt")

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)


time       WSPD
0    2012-01-01   1.595833
1    2012-01-02   3.631818
2    2012-01-03   3.058333
3    2012-01-04   2.629167
4    2012-01-05   3.387500
..          ...        ...
140  2012-12-27  10.887500
141  2012-12-28   5.126087
142  2012-12-29   3.704167
143  2012-12-30   3.520833
144  2012-12-31   4.604545

[145 rows x 2 columns]

In [8]:
#For 46025
# Generate a complete date range for 2010
all_dates = pd.date_range(start="2008-03-05", end="2023-12-31")

# Find the missing date
missing_date = all_dates.difference(fin_df['time'])
print("Missing date:", missing_date)
print(f'There are {len(missing_date)} missing dates')

Missing date: DatetimeIndex(['2010-03-02', '2012-04-01', '2012-04-02', '2012-04-03',
               '2012-04-04', '2012-04-05', '2012-04-06', '2012-04-07',
               '2012-04-08', '2012-04-09',
               ...
               '2012-11-19', '2012-11-20', '2012-11-21', '2012-11-22',
               '2012-11-23', '2021-03-10', '2021-03-11', '2021-03-12',
               '2021-03-13', '2021-03-14'],
              dtype='datetime64[ns]', length=227, freq=None)
There are 227 missing dates


In [9]:
#For 46025
# Generate a complete date range for 2010
all_dates = pd.date_range(start="2008-03-05", end="2023-12-31")

# Find the missing date
missing_date = all_dates.difference(fin_df['time'])
print("Missing date:", missing_date)
print(f'There are {len(missing_date)} missing dates')

Missing date: DatetimeIndex(['2010-03-02', '2012-04-01', '2012-04-02', '2012-04-03',
               '2012-04-04', '2012-04-05', '2012-04-06', '2012-04-07',
               '2012-04-08', '2012-04-09',
               ...
               '2012-11-19', '2012-11-20', '2012-11-21', '2012-11-22',
               '2012-11-23', '2021-03-10', '2021-03-11', '2021-03-12',
               '2021-03-13', '2021-03-14'],
              dtype='datetime64[ns]', length=227, freq=None)
There are 227 missing dates


In [10]:
#For La jolla

fin_df = process_wind_file("Data/Wind_Scrip/wind2008.txt")
for i in range(2009, 2024, 1):
    #print(i)
    fin_df = pd.concat([fin_df, process_wind_file("Data/Wind_Scrip/wind" + str(i) + ".txt")])
fin_df

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/2421531246.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated a

time      WSPD
0    2008-03-05  2.218182
1    2008-03-06  1.208333
2    2008-03-07  1.378947
3    2008-03-08  1.768421
4    2008-03-09  1.558333
..          ...       ...
360  2023-12-27  1.208333
361  2023-12-28  2.466667
362  2023-12-29  1.579167
363  2023-12-30  2.400000
364  2023-12-31  2.962500

[5289 rows x 2 columns]

In [11]:
all_dates = pd.date_range(start="2008-03-05", end="2023-12-31")

# Find the missing date
missing_date_lj = all_dates.difference(fin_df['time'])
print("Missing date:", missing_date_lj)
print(f'There are {len(missing_date_lj)} missing dates')

#NOAA Tide gauge 

Missing date: DatetimeIndex(['2008-03-16', '2008-04-02', '2008-04-03', '2008-04-04',
               '2008-04-05', '2008-04-06', '2008-04-07', '2008-04-08',
               '2008-04-09', '2008-04-10',
               ...
               '2017-08-10', '2019-10-13', '2021-03-10', '2021-03-11',
               '2021-03-12', '2021-03-13', '2021-03-14', '2021-03-15',
               '2021-03-16', '2022-11-09'],
              dtype='datetime64[ns]', length=491, freq=None)
There are 491 missing dates


In [12]:
#Mising dates overlap between 46025 and la jolla
missing_date_overlap = set(missing_date_lj) & set(missing_date)
missing_date_overlap

{Timestamp('2010-03-02 00:00:00'),
 Timestamp('2012-09-05 00:00:00'),
 Timestamp('2012-09-06 00:00:00'),
 Timestamp('2012-09-07 00:00:00'),
 Timestamp('2012-09-08 00:00:00'),
 Timestamp('2012-09-09 00:00:00'),
 Timestamp('2012-09-10 00:00:00'),
 Timestamp('2012-09-11 00:00:00'),
 Timestamp('2012-09-12 00:00:00'),
 Timestamp('2012-09-13 00:00:00'),
 Timestamp('2012-09-14 00:00:00'),
 Timestamp('2012-09-15 00:00:00'),
 Timestamp('2012-09-16 00:00:00'),
 Timestamp('2012-09-17 00:00:00'),
 Timestamp('2012-09-18 00:00:00'),
 Timestamp('2012-09-19 00:00:00'),
 Timestamp('2012-09-20 00:00:00'),
 Timestamp('2021-03-10 00:00:00'),
 Timestamp('2021-03-11 00:00:00'),
 Timestamp('2021-03-12 00:00:00'),
 Timestamp('2021-03-13 00:00:00'),
 Timestamp('2021-03-14 00:00:00')}

# Prep data for MCVM

In [13]:
def process_wind_file_all_col(filepath):
    df = pd.read_table(filepath, delim_whitespace=True)
    df = df.drop(index=df.index[0])
    df['#YY'] = df['#YY'].apply(int)
    #print((filepath[14:18]))
    df = df[df['#YY'] == int(filepath[20:24])]

    for col in df.columns:
        df[col] = pd.to_numeric(df[col], errors='coerce')
    df = df.groupby(['MM','DD','#YY']).mean().reset_index()
    df.rename(columns={'#YY': 'year', 'MM': 'month', 'DD': 'day'}, inplace=True)
    #add time to df which has datetime
    df['time'] = pd.to_datetime(df[['year', 'month', 'day']])
    df['time'] = df['time'].dt.date
    return df.drop(columns=['month','day','year','hh','mm'])

In [14]:
#create df for 46025
fin_df_46025 = process_wind_file_all_col("Data/Wind_46025/wind2008.txt")
for i in range(2009, 2024, 1):
    #print(i)
    fin_df_46025 = pd.concat([fin_df_46025, process_wind_file_all_col("Data/Wind_46025/wind" + str(i) + ".txt")])
rename = dict()
for columns in fin_df_46025.columns:
    if columns != 'time':
        rename[columns] = columns + '_46025'
fin_df_46025 = fin_df_46025.rename(columns=rename)
fin_df_46025

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated a

WDIR_46025  WSPD_46025  GST_46025  WVHT_46025  DPD_46025  APD_46025  \
0    109.000000    3.687500   4.612500    1.068750  13.100000   5.997917   
1     84.250000    3.758333   4.441667    0.610000  12.515000   4.919583   
2    114.916667    2.050000   2.579167    0.538333  13.334583   8.115417   
3    147.333333    4.012500   4.850000    1.099583  13.639167   8.988333   
4    224.083333    6.833333   8.475000    2.325000   9.494167   6.562083   
..          ...         ...        ...         ...        ...        ...   
360  299.527778    2.990972   4.049306   66.470694  70.774306  69.021250   
361  302.743056    2.878472   4.158333   66.702431  70.883889  69.448403   
362  250.229167    2.540972   4.306944   67.048056  71.243264  69.757778   
363  207.361111    4.835417   6.879167   67.012778  71.349653  69.660972   
364  240.993056    3.921528   5.836111   67.093889  70.939306  69.257639   

      MWD_46025   PRES_46025  ATMP_46025  WTMP_46025  DEWP_46025  VIS_46025  \
0    256.500000  1020.658333   14.979167   13.379167  214.766667       99.0   
1    207.416667  1018.845833   15.095833   13.487500   48.883333       99.0   
2    223.375000  1018.104167   13.825000   13.554167   10.858333       99.0   
3    258.083333  1017.620833   13.558333   13.641667   11.883333       99.0   
4    238.916667  1013.025000   13.700000   13.620833   12.716667       99.0   
..          ...          ...         ...         ...         ...        ...   
360  751.979167  1021.257639   15.438889   23.368056   13.327778       99.0   
361  751.062500  1021.979167   15.145139   16.436806   12.409722       99.0   
362  753.708333  1020.238194   15.186111   23.611806   13.581944       99.0   
363  752.652778  1018.888194   14.953472   23.575000   13.088889       99.0   
364  753.083333  1019.456944   15.296528   23.526389   11.974306       99.0   

     TIDE_46025        time  
0          99.0  2008-01-01  
1          99.0  2008-01-02  
2          99.0  2008-01-03  
3          99.0  2008-01-04  
4          99.0  2008-01-05  
..          ...         ...  
360        99.0  2023-12-27  
361        99.0  2023-12-28  
362        99.0  2023-12-29  
363        99.0  2023-12-30  
364        99.0  2023-12-31  

[5617 rows x 14 columns]

In [15]:
#create df for lajolla
fin_df_lj = process_wind_file_all_col("Data/Wind_Scrip/wind2008.txt")
for i in range(2009, 2024, 1):
    #print(i)
    fin_df_lj = pd.concat([fin_df_lj, process_wind_file_all_col("Data/Wind_Scrip/wind" + str(i) + ".txt")])
rename = dict()
for columns in fin_df_lj.columns:
    if columns != 'time':
        rename[columns] = columns + '_lj'
fin_df_lj = fin_df_lj.rename(columns=rename)
fin_df_lj

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  df = pd.read_table(filepath, delim_whitespace=True)
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/3243319043.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_table is deprecated a

WDIR_lj   WSPD_lj    GST_lj    WVHT_lj     DPD_lj     APD_lj  MWD_lj  \
0    166.727273  2.218182  3.568182  99.000000  99.000000  99.000000   999.0   
1    191.458333  1.208333  2.200000  99.000000  99.000000  99.000000   999.0   
2    162.894737  1.378947  2.742105  99.000000  99.000000  99.000000   999.0   
3    186.210526  1.768421  2.705263  99.000000  99.000000  99.000000   999.0   
4    176.333333  1.558333  2.833333  99.000000  99.000000  99.000000   999.0   
..          ...       ...       ...        ...        ...        ...     ...   
360  143.333333  1.208333  2.400000   0.770833  12.993333   8.341250   999.0   
361  229.291667  2.466667  3.912500   0.950417  13.167083   9.065417   999.0   
362  210.708333  1.579167  2.737500   1.661667  13.820000   8.688750   999.0   
363  172.958333  2.400000  3.958333   1.398333  13.394583   8.941250   999.0   
364  206.208333  2.962500  4.666667   1.710417  12.807083   7.801667   999.0   

     PRES_lj     ATMP_lj  WTMP_lj  DEWP_lj  VIS_lj  TIDE_lj        time  
0     9999.0   13.168182    999.0    999.0    99.0     99.0  2008-03-05  
1     9999.0   14.179167    999.0    999.0    99.0     99.0  2008-03-06  
2     9999.0   14.868421    999.0    999.0    99.0     99.0  2008-03-07  
3     9999.0   14.768421    999.0    999.0    99.0     99.0  2008-03-08  
4     9999.0   14.408333    999.0    999.0    99.0     99.0  2008-03-09  
..       ...         ...      ...      ...     ...      ...         ...  
360   9999.0  999.000000    999.0    999.0    99.0     99.0  2023-12-27  
361   9999.0  999.000000    999.0    999.0    99.0     99.0  2023-12-28  
362   9999.0  999.000000    999.0    999.0    99.0     99.0  2023-12-29  
363   9999.0  999.000000    999.0    999.0    99.0     99.0  2023-12-30  
364   9999.0  999.000000    999.0    999.0    99.0     99.0  2023-12-31  

[5289 rows x 14 columns]

In [16]:
all_wind_cols = fin_df_lj.merge(fin_df_46025,how='outer' ,left_on='time', right_on='time')
all_wind_cols

WDIR_lj   WSPD_lj    GST_lj   WVHT_lj     DPD_lj    APD_lj  MWD_lj  \
0            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
1            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
2            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
3            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
4            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
...          ...       ...       ...       ...        ...       ...     ...   
5817  143.333333  1.208333  2.400000  0.770833  12.993333  8.341250   999.0   
5818  229.291667  2.466667  3.912500  0.950417  13.167083  9.065417   999.0   
5819  210.708333  1.579167  2.737500  1.661667  13.820000  8.688750   999.0   
5820  172.958333  2.400000  3.958333  1.398333  13.394583  8.941250   999.0   
5821  206.208333  2.962500  4.666667  1.710417  12.807083  7.801667   999.0   

      PRES_lj  ATMP_lj  WTMP_lj  ...  WVHT_46025  DPD_46025  APD_46025  \
0         NaN      NaN      NaN  ...    1.068750  13.100000   5.997917   
1         NaN      NaN      NaN  ...    0.610000  12.515000   4.919583   
2         NaN      NaN      NaN  ...    0.538333  13.334583   8.115417   
3         NaN      NaN      NaN  ...    1.099583  13.639167   8.988333   
4         NaN      NaN      NaN  ...    2.325000   9.494167   6.562083   
...       ...      ...      ...  ...         ...        ...        ...   
5817   9999.0    999.0    999.0  ...   66.470694  70.774306  69.021250   
5818   9999.0    999.0    999.0  ...   66.702431  70.883889  69.448403   
5819   9999.0    999.0    999.0  ...   67.048056  71.243264  69.757778   
5820   9999.0    999.0    999.0  ...   67.012778  71.349653  69.660972   
5821   9999.0    999.0    999.0  ...   67.093889  70.939306  69.257639   

       MWD_46025   PRES_46025  ATMP_46025  WTMP_46025  DEWP_46025  VIS_46025  \
0     256.500000  1020.658333   14.979167   13.379167  214.766667       99.0   
1     207.416667  1018.845833   15.095833   13.487500   48.883333       99.0   
2     223.375000  1018.104167   13.825000   13.554167   10.858333       99.0   
3     258.083333  1017.620833   13.558333   13.641667   11.883333       99.0   
4     238.916667  1013.025000   13.700000   13.620833   12.716667       99.0   
...          ...          ...         ...         ...         ...        ...   
5817  751.979167  1021.257639   15.438889   23.368056   13.327778       99.0   
5818  751.062500  1021.979167   15.145139   16.436806   12.409722       99.0   
5819  753.708333  1020.238194   15.186111   23.611806   13.581944       99.0   
5820  752.652778  1018.888194   14.953472   23.575000   13.088889       99.0   
5821  753.083333  1019.456944   15.296528   23.526389   11.974306       99.0   

      TIDE_46025  
0           99.0  
1           99.0  
2           99.0  
3           99.0  
4           99.0  
...          ...  
5817        99.0  
5818        99.0  
5819        99.0  
5820        99.0  
5821        99.0  

[5822 rows x 27 columns]

In [17]:
#Check rows where all values are NaN
nan_rows = all_wind_cols[all_wind_cols.isna().all(axis=1)]
nan_rows

Empty DataFrame
Columns: [WDIR_lj, WSPD_lj, GST_lj, WVHT_lj, DPD_lj, APD_lj, MWD_lj, PRES_lj, ATMP_lj, WTMP_lj, DEWP_lj, VIS_lj, TIDE_lj, time, WDIR_46025, WSPD_46025, GST_46025, WVHT_46025, DPD_46025, APD_46025, MWD_46025, PRES_46025, ATMP_46025, WTMP_46025, DEWP_46025, VIS_46025, TIDE_46025]
Index: []

[0 rows x 27 columns]

In [18]:
#Sanity check to see how many missing dates
all_dates = pd.date_range(start="2008-01-01", end="2023-12-31")

# Find the missing date
missing_date = all_dates.difference(all_wind_cols['time'])
print("Missing date:", missing_date)
print(f'There are {len(missing_date)} missing dates')

Missing date: DatetimeIndex(['2010-03-02', '2012-09-05', '2012-09-06', '2012-09-07',
               '2012-09-08', '2012-09-09', '2012-09-10', '2012-09-11',
               '2012-09-12', '2012-09-13', '2012-09-14', '2012-09-15',
               '2012-09-16', '2012-09-17', '2012-09-18', '2012-09-19',
               '2012-09-20', '2021-03-10', '2021-03-11', '2021-03-12',
               '2021-03-13', '2021-03-14'],
              dtype='datetime64[ns]', freq=None)
There are 22 missing dates


In [19]:
#add in missing rows
all_dates
curr_row = 0
all_wind_cols['time'] = pd.to_datetime(all_wind_cols['time'], errors='coerce')
all_wind_cols = all_wind_cols.assign(new_time=np.arange(all_wind_cols.shape[0]))
for i, date in enumerate(all_dates):
    if (date.date() in all_wind_cols['time'].dt.date.values):
        all_wind_cols['new_time'].iloc[curr_row] = i
        curr_row += 1
    else:
        all_wind_cols.loc[len(all_wind_cols)] = np.nan 
        all_wind_cols['new_time'].iloc[-1] = i
all_wind_cols

/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/489161114.py:8: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  all_wind_cols['new_time'].iloc[curr_row] = i
/var/folders/5y/74w_zv855875xvjtmhp4g1xw0000gn/T/ipykernel_97887/4891

WDIR_lj  WSPD_lj  GST_lj  WVHT_lj  DPD_lj  APD_lj  MWD_lj  PRES_lj  \
0         NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1         NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
2         NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
3         NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
4         NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
...       ...      ...     ...      ...     ...     ...     ...      ...   
5839      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
5840      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
5841      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
5842      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
5843      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   

      ATMP_lj  WTMP_lj  ...  DPD_46025  APD_46025   MWD_46025   PRES_46025  \
0         NaN      NaN  ...  13.100000   5.997917  256.500000  1020.658333   
1         NaN      NaN  ...  12.515000   4.919583  207.416667  1018.845833   
2         NaN      NaN  ...  13.334583   8.115417  223.375000  1018.104167   
3         NaN      NaN  ...  13.639167   8.988333  258.083333  1017.620833   
4         NaN      NaN  ...   9.494167   6.562083  238.916667  1013.025000   
...       ...      ...  ...        ...        ...         ...          ...   
5839      NaN      NaN  ...        NaN        NaN         NaN          NaN   
5840      NaN      NaN  ...        NaN        NaN         NaN          NaN   
5841      NaN      NaN  ...        NaN        NaN         NaN          NaN   
5842      NaN      NaN  ...        NaN        NaN         NaN          NaN   
5843      NaN      NaN  ...        NaN        NaN         NaN          NaN   

      ATMP_46025  WTMP_46025  DEWP_46025  VIS_46025  TIDE_46025  new_time  
0      14.979167   13.379167  214.766667       99.0        99.0       0.0  
1      15.095833   13.487500   48.883333       99.0        99.0       1.0  
2      13.825000   13.554167   10.858333       99.0        99.0       2.0  
3      13.558333   13.641667   11.883333       99.0        99.0       3.0  
4      13.700000   13.620833   12.716667       99.0        99.0       4.0  
...          ...         ...         ...        ...         ...       ...  
5839         NaN         NaN         NaN        NaN         NaN    4817.0  
5840         NaN         NaN         NaN        NaN         NaN    4818.0  
5841         NaN         NaN         NaN        NaN         NaN    4819.0  
5842         NaN         NaN         NaN        NaN         NaN    4820.0  
5843         NaN         NaN         NaN        NaN         NaN    4821.0  

[5844 rows x 28 columns]

In [20]:
#formatting
all_wind_cols = all_wind_cols.sort_values('new_time')
all_wind_cols['time'] = all_wind_cols['new_time'].astype(int)
all_wind_cols = all_wind_cols.drop(columns=['new_time'])
all_wind_cols = all_wind_cols.set_index('time')
all_wind_cols

WDIR_lj   WSPD_lj    GST_lj   WVHT_lj     DPD_lj    APD_lj  MWD_lj  \
time                                                                            
0.0            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
1.0            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
2.0            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
3.0            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
4.0            NaN       NaN       NaN       NaN        NaN       NaN     NaN   
...            ...       ...       ...       ...        ...       ...     ...   
5839.0  143.333333  1.208333  2.400000  0.770833  12.993333  8.341250   999.0   
5840.0  229.291667  2.466667  3.912500  0.950417  13.167083  9.065417   999.0   
5841.0  210.708333  1.579167  2.737500  1.661667  13.820000  8.688750   999.0   
5842.0  172.958333  2.400000  3.958333  1.398333  13.394583  8.941250   999.0   
5843.0  206.208333  2.962500  4.666667  1.710417  12.807083  7.801667   999.0   

        PRES_lj  ATMP_lj  WTMP_lj  ...  WVHT_46025  DPD_46025  APD_46025  \
time                               ...                                     
0.0         NaN      NaN      NaN  ...    1.068750  13.100000   5.997917   
1.0         NaN      NaN      NaN  ...    0.610000  12.515000   4.919583   
2.0         NaN      NaN      NaN  ...    0.538333  13.334583   8.115417   
3.0         NaN      NaN      NaN  ...    1.099583  13.639167   8.988333   
4.0         NaN      NaN      NaN  ...    2.325000   9.494167   6.562083   
...         ...      ...      ...  ...         ...        ...        ...   
5839.0   9999.0    999.0    999.0  ...   66.470694  70.774306  69.021250   
5840.0   9999.0    999.0    999.0  ...   66.702431  70.883889  69.448403   
5841.0   9999.0    999.0    999.0  ...   67.048056  71.243264  69.757778   
5842.0   9999.0    999.0    999.0  ...   67.012778  71.349653  69.660972   
5843.0   9999.0    999.0    999.0  ...   67.093889  70.939306  69.257639   

         MWD_46025   PRES_46025  ATMP_46025  WTMP_46025  DEWP_46025  \
time                                                                  
0.0     256.500000  1020.658333   14.979167   13.379167  214.766667   
1.0     207.416667  1018.845833   15.095833   13.487500   48.883333   
2.0     223.375000  1018.104167   13.825000   13.554167   10.858333   
3.0     258.083333  1017.620833   13.558333   13.641667   11.883333   
4.0     238.916667  1013.025000   13.700000   13.620833   12.716667   
...            ...          ...         ...         ...         ...   
5839.0  751.979167  1021.257639   15.438889   23.368056   13.327778   
5840.0  751.062500  1021.979167   15.145139   16.436806   12.409722   
5841.0  753.708333  1020.238194   15.186111   23.611806   13.581944   
5842.0  752.652778  1018.888194   14.953472   23.575000   13.088889   
5843.0  753.083333  1019.456944   15.296528   23.526389   11.974306   

        VIS_46025  TIDE_46025  
time                           
0.0          99.0        99.0  
1.0          99.0        99.0  
2.0          99.0        99.0  
3.0          99.0        99.0  
4.0          99.0        99.0  
...           ...         ...  
5839.0       99.0        99.0  
5840.0       99.0        99.0  
5841.0       99.0        99.0  
5842.0       99.0        99.0  
5843.0       99.0        99.0  

[5844 rows x 26 columns]

In [21]:
#Sanity check 2: Check rows where all values are NaN
nan_rows = all_wind_cols[all_wind_cols.isna().all(axis=1)]
nan_rows

WDIR_lj  WSPD_lj  GST_lj  WVHT_lj  DPD_lj  APD_lj  MWD_lj  PRES_lj  \
time                                                                         
791.0       NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1709.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1710.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1711.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1712.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1713.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1714.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1715.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1716.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1717.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1718.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1719.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1720.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1721.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1722.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1723.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
1724.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
4817.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
4818.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
4819.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
4820.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   
4821.0      NaN      NaN     NaN      NaN     NaN     NaN     NaN      NaN   

        ATMP_lj  WTMP_lj  ...  WVHT_46025  DPD_46025  APD_46025  MWD_46025  \
time                      ...                                                
791.0       NaN      NaN  ...         NaN        NaN        NaN        NaN   
1709.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1710.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1711.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1712.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1713.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1714.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1715.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1716.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1717.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1718.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1719.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1720.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1721.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1722.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1723.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
1724.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
4817.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
4818.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
4819.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
4820.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   
4821.0      NaN      NaN  ...         NaN        NaN        NaN        NaN   

        PRES_46025  ATMP_46025  WTMP_46025  DEWP_46025  VIS_46025  TIDE_46025  
time                                                                           
791.0          NaN         NaN         NaN         NaN        NaN         NaN  
1709.0         NaN    

In [22]:
#Convert to CSV
all_wind_cols.to_csv('Data/wind_data_w_gaps.csv', index=True)

In [23]:
print(fin_df.isna().sum())

time    0
WSPD    0
dtype: int64
